In [1]:
import pysmile
import pysmile_license
import numpy as np
import pandas as pd

from network_functions import calculate_network_utilities, new_screening_strategy, old_screening_strategy, create_folders_logger
from simulations import plot_classification_results
from plots import plot_estimations_w_error_bars, plot_screening_counts

from preprocessing import preprocessing
from concurrent.futures import ProcessPoolExecutor, as_completed
from tqdm import tqdm
import matplotlib.pyplot as plt

import yaml
with open('config.yaml', 'r') as file:
    cfg = yaml.safe_load(file)

import argparse
import pdb
import matplotlib
matplotlib.use('Agg')

import logging
import datetime 
import os

In [2]:
# from main import main
from use_case_new_strategy import use_case_new_strategy
from full_example import full_example
from update import update_influence_diagram
from network_functions import create_folders_logger
from sens_analysis_elicitation import sens_analysis_elicitation
from sens_analysis_PE_method import sens_analysis_PE_method

### Preferences model

## Use cases

### Individual cases

**Benchmark patient**

In [3]:
label = 'notebook_benchmark_patient'
logger, log_dir = create_folders_logger(label = label, output_dir = 'notebook/' + label, date = False, time = False)

update_influence_diagram(
    model_type = cfg["model_type"],
    value_function = cfg["value_function"],
    elicit = cfg["elicit"],
    noise = cfg["noise"],
    calculate_info_values= cfg["calculate_info_values"],
    ref_patient_chars = cfg["patient_chars"],
    new_test = cfg["new_test"],
    logger = logger,
    output_dir = 'notebook/' + label
)

2024-11-20 11:05:43,471 - INFO - Model type: linear
2024-11-20 11:05:43,472 - INFO - Reading network...
2024-11-20 11:05:43,486 - INFO - Calculating information values...
2024-11-20 11:06:34,380 - INFO - Eliciting value of comfort...
2024-11-20 11:06:34,381 - INFO - No elicitation of lambda values, taking default values...
2024-11-20 11:06:34,382 - INFO - Adding noise to the lambda values...
2024-11-20 11:06:34,384 - INFO - Lambda values: [7.         4.01194248 6.80198452 4.01194248 6.80198452 4.01194248
 6.80198452 4.01194248 6.80198452 4.01194248 4.16848007 4.01194248
 4.16848007 4.01194248]
2024-11-20 11:06:34,384 - INFO - Saving network...
2024-11-20 11:06:34,414 - INFO - Plotting info functions...
2024-11-20 11:07:06,360 - INFO - Calculating final utilities...
2024-11-20 11:07:06,367 - INFO - Best info: 15.299634978175163
2024-11-20 11:07:06,368 - INFO - Worst info: 4.450147717014403e-308
2024-11-20 11:07:06,368 - INFO - PE info: 4
2024-11-20 11:07:06,369 - INFO - v_best: 104.0678

**Benchmark patient risk seeking**

In [7]:
label = 'notebook_benchmark_risk_seeking'
logger, log_dir = create_folders_logger(label = label, output_dir = 'notebook/' + label, date = False, time = False)

update_influence_diagram(
    model_type = cfg["model_type"],
    value_function = cfg["value_function"],
    elicit = cfg["elicit"],
    noise = cfg["noise"],
    calculate_info_values= cfg["calculate_info_values"],
    ref_patient_chars = cfg["patient_chars"],
    new_test = cfg["new_test"],
    logger = logger,
    output_dir = 'notebook/' + label,
    change_risk_param=True,
    rho_param= 0.005
)

2024-11-20 08:57:42,748 - INFO - Model type: linear
2024-11-20 08:57:42,748 - INFO - Model type: linear
2024-11-20 08:57:42,748 - INFO - Model type: linear
2024-11-20 08:57:42,750 - INFO - Reading network...
2024-11-20 08:57:42,750 - INFO - Reading network...
2024-11-20 08:57:42,750 - INFO - Reading network...
2024-11-20 08:57:42,766 - INFO - Calculating information values...
2024-11-20 08:57:42,766 - INFO - Calculating information values...
2024-11-20 08:57:42,766 - INFO - Calculating information values...
2024-11-20 08:58:35,222 - INFO - Eliciting value of comfort...
2024-11-20 08:58:35,222 - INFO - Eliciting value of comfort...
2024-11-20 08:58:35,222 - INFO - Eliciting value of comfort...
2024-11-20 08:58:35,225 - INFO - No elicitation of lambda values, taking default values...
2024-11-20 08:58:35,225 - INFO - No elicitation of lambda values, taking default values...
2024-11-20 08:58:35,225 - INFO - No elicitation of lambda values, taking default values...
2024-11-20 08:58:35,227 -

**Benchmark patient added evidence**

In [8]:
label = 'notebook_benchmark_addded_ev'
logger, log_dir = create_folders_logger(label = label, output_dir = 'notebook/' + label, date = False, time = False)

patient_chars = cfg["patient_chars"]
patient_chars["Diabetes"] = True
patient_chars["Hypertension"] = True

update_influence_diagram(
    model_type = cfg["model_type"],
    value_function = cfg["value_function"],
    elicit = cfg["elicit"],
    noise = cfg["noise"],
    calculate_info_values= cfg["calculate_info_values"],
    ref_patient_chars = patient_chars,
    new_test = cfg["new_test"],
    logger = logger,
    output_dir = 'notebook/' + label,
)

2024-11-20 09:00:17,951 - INFO - Model type: linear
2024-11-20 09:00:17,951 - INFO - Model type: linear
2024-11-20 09:00:17,951 - INFO - Model type: linear
2024-11-20 09:00:17,951 - INFO - Model type: linear
2024-11-20 09:00:17,953 - INFO - Reading network...
2024-11-20 09:00:17,953 - INFO - Reading network...
2024-11-20 09:00:17,953 - INFO - Reading network...
2024-11-20 09:00:17,953 - INFO - Reading network...
2024-11-20 09:00:17,968 - INFO - Calculating information values...
2024-11-20 09:00:17,968 - INFO - Calculating information values...
2024-11-20 09:00:17,968 - INFO - Calculating information values...
2024-11-20 09:00:17,968 - INFO - Calculating information values...
2024-11-20 09:01:09,049 - INFO - Eliciting value of comfort...
2024-11-20 09:01:09,049 - INFO - Eliciting value of comfort...
2024-11-20 09:01:09,049 - INFO - Eliciting value of comfort...
2024-11-20 09:01:09,049 - INFO - Eliciting value of comfort...
2024-11-20 09:01:09,051 - INFO - No elicitation of lambda values

**Exogenous variable p = 0.02**

In [ ]:
label = 'notebook_exogenous_var_002'
logger, log_dir = create_folders_logger(label = label, output_dir = 'notebook/' + label, date = False, time = False)

exog_char ={"Age": "age_2_young", 
    "Sex": "M",
    "SES": "ses_0",
    "SD": "SD_1_short",
    "PA": "PA_1",
    "Depression": False,
    "Smoking": "sm_1_not_smoker",
    "Anxiety": False,
    "BMI": "bmi_1_underweight",
    "Alcohol": "high",
    "Diabetes": False,
    "Hypertension": False,
    "Hyperchol_": False,
    }


update_influence_diagram(
    model_type = cfg["model_type"],
    value_function = cfg["value_function"],
    elicit = cfg["elicit"],
    noise = cfg["noise"],
    calculate_info_values= cfg["calculate_info_values"],
    ref_patient_chars = exog_char,
    new_test = cfg["new_test"],
    logger = logger,
    output_dir = 'notebook/' + label,
    exogenous_var_prob= 0.02
)

2024-11-19 19:12:57,185 - INFO - Model type: linear
2024-11-19 19:12:57,185 - INFO - Model type: linear
2024-11-19 19:12:57,185 - INFO - Model type: linear
2024-11-19 19:12:57,185 - INFO - Model type: linear
2024-11-19 19:12:57,185 - INFO - Model type: linear
2024-11-19 19:12:57,187 - INFO - Reading network...
2024-11-19 19:12:57,187 - INFO - Reading network...
2024-11-19 19:12:57,187 - INFO - Reading network...
2024-11-19 19:12:57,187 - INFO - Reading network...
2024-11-19 19:12:57,187 - INFO - Reading network...
2024-11-19 19:12:57,204 - INFO - Calculating information values...
2024-11-19 19:12:57,204 - INFO - Calculating information values...
2024-11-19 19:12:57,204 - INFO - Calculating information values...
2024-11-19 19:12:57,204 - INFO - Calculating information values...
2024-11-19 19:12:57,204 - INFO - Calculating information values...
2024-11-19 19:13:50,212 - INFO - Eliciting value of comfort...
2024-11-19 19:13:50,212 - INFO - Eliciting value of comfort...
2024-11-19 19:13:50

**Exogenous variable p = 0.1**

In [ ]:
label = 'notebook_exogenous_var_01'
logger, log_dir = create_folders_logger(label = label, output_dir = 'notebook/' + label, date = False, time = False)

exog_char ={"Age": "age_2_young", 
    "Sex": "M",
    "SES": "ses_0",
    "SD": "SD_1_short",
    "PA": "PA_1",
    "Depression": False,
    "Smoking": "sm_1_not_smoker",
    "Anxiety": False,
    "BMI": "bmi_1_underweight",
    "Alcohol": "high",
    "Diabetes": False,
    "Hypertension": False,
    "Hyperchol_": False,
    }

update_influence_diagram(
    model_type = cfg["model_type"],
    value_function = cfg["value_function"],
    elicit = cfg["elicit"],
    noise = cfg["noise"],
    calculate_info_values= cfg["calculate_info_values"],
    ref_patient_chars = exog_char,
    new_test = cfg["new_test"],
    logger = logger,
    output_dir = 'notebook/' + label,
    exogenous_var_prob= 0.1
)

2024-11-19 19:14:24,995 - INFO - Model type: linear
2024-11-19 19:14:24,995 - INFO - Model type: linear
2024-11-19 19:14:24,995 - INFO - Model type: linear
2024-11-19 19:14:24,995 - INFO - Model type: linear
2024-11-19 19:14:24,995 - INFO - Model type: linear
2024-11-19 19:14:24,995 - INFO - Model type: linear
2024-11-19 19:14:24,998 - INFO - Reading network...
2024-11-19 19:14:24,998 - INFO - Reading network...
2024-11-19 19:14:24,998 - INFO - Reading network...
2024-11-19 19:14:24,998 - INFO - Reading network...
2024-11-19 19:14:24,998 - INFO - Reading network...
2024-11-19 19:14:24,998 - INFO - Reading network...
2024-11-19 19:14:25,014 - INFO - Calculating information values...
2024-11-19 19:14:25,014 - INFO - Calculating information values...
2024-11-19 19:14:25,014 - INFO - Calculating information values...
2024-11-19 19:14:25,014 - INFO - Calculating information values...
2024-11-19 19:14:25,014 - INFO - Calculating information values...
2024-11-19 19:14:25,014 - INFO - Calculat

### Assessing the French strategy

**Patient 1**

In [ ]:
label = 'notebook_4_2_patient_1'
logger, log_dir = create_folders_logger(label = label, output_dir = 'notebook/' + label, date = False, time = False)

patient_chars = {
    "Age": "age_5_old_adult", 
    "Sex": "M",
    "SD": "SD_2_normal",
    "PA": "PA_2",
    "Smoking": "sm_1_not_smoker",
    "BMI": "bmi_2_normal",
    "Alcohol": "low",
    "Diabetes": False,
    "Hypertension": False,
}

update_influence_diagram(
    model_type = cfg["model_type"],
    value_function = cfg["value_function"],
    elicit = cfg["elicit"],
    noise = cfg["noise"],
    calculate_info_values= cfg["calculate_info_values"],
    ref_patient_chars = patient_chars,
    new_test = cfg["new_test"],
    logger = logger,
    output_dir = 'notebook/' + label
)

2024-11-19 19:15:53,729 - INFO - Model type: linear
2024-11-19 19:15:53,729 - INFO - Model type: linear
2024-11-19 19:15:53,729 - INFO - Model type: linear
2024-11-19 19:15:53,729 - INFO - Model type: linear
2024-11-19 19:15:53,729 - INFO - Model type: linear
2024-11-19 19:15:53,729 - INFO - Model type: linear
2024-11-19 19:15:53,729 - INFO - Model type: linear
2024-11-19 19:15:53,733 - INFO - Reading network...
2024-11-19 19:15:53,733 - INFO - Reading network...
2024-11-19 19:15:53,733 - INFO - Reading network...
2024-11-19 19:15:53,733 - INFO - Reading network...
2024-11-19 19:15:53,733 - INFO - Reading network...
2024-11-19 19:15:53,733 - INFO - Reading network...
2024-11-19 19:15:53,733 - INFO - Reading network...
2024-11-19 19:15:53,755 - INFO - Calculating information values...
2024-11-19 19:15:53,755 - INFO - Calculating information values...
2024-11-19 19:15:53,755 - INFO - Calculating information values...
2024-11-19 19:15:53,755 - INFO - Calculating information values...
2024

**Patient 2**

In [ ]:
label = 'notebook_4_2_patient_2'
logger, log_dir = create_folders_logger(label = label, output_dir = 'notebook/' + label, date = False, time = False)

patient_chars = {
    "Age": "age_4_adult", 
    "Sex": "M",
    "SD": "SD_2_normal",
    "PA": "PA_2",
    "Smoking": "sm_1_not_smoker",
    "BMI": "bmi_2_normal",
    "Alcohol": "low",
    "Diabetes": True,
    "Hypertension": True,
}

update_influence_diagram(
    model_type = cfg["model_type"],
    value_function = cfg["value_function"],
    elicit = cfg["elicit"],
    noise = cfg["noise"],
    calculate_info_values= cfg["calculate_info_values"],
    ref_patient_chars = patient_chars,
    new_test = cfg["new_test"],
    logger = logger,
    output_dir = 'notebook/' + label
)

2024-11-19 19:17:26,384 - INFO - Model type: linear
2024-11-19 19:17:26,384 - INFO - Model type: linear
2024-11-19 19:17:26,384 - INFO - Model type: linear
2024-11-19 19:17:26,384 - INFO - Model type: linear
2024-11-19 19:17:26,384 - INFO - Model type: linear
2024-11-19 19:17:26,384 - INFO - Model type: linear
2024-11-19 19:17:26,384 - INFO - Model type: linear
2024-11-19 19:17:26,384 - INFO - Model type: linear
2024-11-19 19:17:26,390 - INFO - Reading network...
2024-11-19 19:17:26,390 - INFO - Reading network...
2024-11-19 19:17:26,390 - INFO - Reading network...
2024-11-19 19:17:26,390 - INFO - Reading network...
2024-11-19 19:17:26,390 - INFO - Reading network...
2024-11-19 19:17:26,390 - INFO - Reading network...
2024-11-19 19:17:26,390 - INFO - Reading network...
2024-11-19 19:17:26,390 - INFO - Reading network...
2024-11-19 19:17:26,418 - INFO - Calculating information values...
2024-11-19 19:17:26,418 - INFO - Calculating information values...
2024-11-19 19:17:26,418 - INFO - C

**Patient 3**

In [ ]:
label = 'notebook_4_2_patient_3'
logger, log_dir = create_folders_logger(label = label)

patient_chars = {
    "Age": "age_4_adult", 
    "Sex": "M",
    "SD": "SD_2_normal",
    "PA": "PA_1",
    "Smoking": "sm_3_ex_smoker",
    "BMI": "bmi_3_overweight",
    "Alcohol": "high",
}

update_influence_diagram(
    model_type = cfg["model_type"],
    value_function = cfg["value_function"],
    elicit = cfg["elicit"],
    noise = cfg["noise"],
    calculate_info_values= cfg["calculate_info_values"],
    ref_patient_chars = patient_chars,
    new_test = cfg["new_test"],
    logger = logger,
    output_dir = 'notebook/' + label
)

2024-11-19 19:19:08,706 - INFO - Model type: linear
2024-11-19 19:19:08,706 - INFO - Model type: linear
2024-11-19 19:19:08,706 - INFO - Model type: linear
2024-11-19 19:19:08,706 - INFO - Model type: linear
2024-11-19 19:19:08,706 - INFO - Model type: linear
2024-11-19 19:19:08,706 - INFO - Model type: linear
2024-11-19 19:19:08,706 - INFO - Model type: linear
2024-11-19 19:19:08,706 - INFO - Model type: linear
2024-11-19 19:19:08,706 - INFO - Model type: linear
2024-11-19 19:19:08,713 - INFO - Reading network...
2024-11-19 19:19:08,713 - INFO - Reading network...
2024-11-19 19:19:08,713 - INFO - Reading network...
2024-11-19 19:19:08,713 - INFO - Reading network...
2024-11-19 19:19:08,713 - INFO - Reading network...
2024-11-19 19:19:08,713 - INFO - Reading network...
2024-11-19 19:19:08,713 - INFO - Reading network...
2024-11-19 19:19:08,713 - INFO - Reading network...
2024-11-19 19:19:08,713 - INFO - Reading network...
2024-11-19 19:19:08,737 - INFO - Calculating information values.

### Designing a national personalised strategy

In [3]:
label = 'notebook_personalised_screening_str'
logger, log_dir = create_folders_logger(label=label, output_dir = 'notebook/' + label, date = False, time = False)

use_case_new_strategy(
    logger = logger,
    output_dir = 'notebook/' + label,
    log_dir = log_dir,
    run_label = ''
)

2024-11-20 09:36:57,809 - INFO - Configuration variables of interest:
2024-11-20 09:36:57,810 - INFO - Single run: True
2024-11-20 09:36:57,810 - INFO - Use all variables: True
2024-11-20 09:36:57,811 - INFO - Use case with new test: False
2024-11-20 09:36:57,811 - INFO - PE method: {'PE_cost': 10, 'PE_info': 4, 'PE_prob': 0.7}
2024-11-20 09:36:57,812 - INFO - Reading the network file...
2024-11-20 09:36:57,827 - INFO - Located at: outputs/linear_rel_point_cond_mut_info_elicitFalse_newtestFalse/decision_models/DM_screening_rel_point_cond_mut_info_linear.xdsl
2024-11-20 09:36:57,827 - INFO - Comfort values: 1 - 4.011942483017116, 2 - 4.168480067521723, 3 - 6.801984517973132, 4 - 7.0
2024-11-20 09:36:58,394 - INFO - All variables are kept in the dataframe for calculation of utilities.
2024-11-20 09:36:58,395 - INFO - Operational limits for the screening strategies: {'No_scr_no_col': inf, 'No_scr_col': 3000, 'gFOBT': 30000, 'FIT': 40000, 'Blood_based': 7000, 'Stool_DNA': 5000, 'CTC': 2000

### Benchmarking of new screening devices

In [3]:
label = 'notebook_benchmark_new_screening'
logger, log_dir = create_folders_logger(label=label, output_dir = 'notebook/' + label, date = False, time = False)

update_influence_diagram(
    model_type = cfg["model_type"],
    value_function = cfg["value_function"],
    elicit = cfg["elicit"],
    noise = cfg["noise"],
    calculate_info_values= cfg["calculate_info_values"],
    ref_patient_chars = cfg["patient_chars"],
    new_test = True,
    logger = logger,
    output_dir = 'notebook/' + label
)

2024-11-20 11:39:12,236 - INFO - Model type: linear
2024-11-20 11:39:12,237 - INFO - Reading network...
2024-11-20 11:39:12,252 - INFO - Calculating information values...
2024-11-20 11:40:09,546 - INFO - Eliciting value of comfort...
2024-11-20 11:40:09,547 - INFO - No elicitation of lambda values, taking default values...
2024-11-20 11:40:09,548 - INFO - Adding noise to the lambda values...
2024-11-20 11:40:09,549 - INFO - Lambda values: [7.         4.01194248 6.80198452 4.01194248 6.80198452 4.01194248
 6.80198452 4.01194248 6.80198452 4.01194248 4.16848007 4.01194248
 4.16848007 4.01194248]
2024-11-20 11:40:09,550 - INFO - Adding new test values...
2024-11-20 11:41:17,222 - INFO - Saving network...
2024-11-20 11:41:17,283 - INFO - Plotting info functions...
2024-11-20 11:42:37,285 - INFO - Calculating final utilities...
2024-11-20 11:42:37,294 - INFO - Best info: 15.299634978175163
2024-11-20 11:42:37,295 - INFO - Worst info: 4.450147717014403e-308
2024-11-20 11:42:37,296 - INFO - P

In [7]:
label = 'notebook_new_test_screening_strategy'
logger, log_dir = create_folders_logger(label=label, output_dir = 'notebook/' + label, date = False, time = False)

use_case_new_strategy(
    use_case_new_test = True,
    output_dir = 'notebook/' + label,
    log_dir = log_dir,
    run_label = ''
)

2024-11-20 10:41:06,370 - INFO - Configuration variables of interest:
2024-11-20 10:41:06,370 - INFO - Configuration variables of interest:
2024-11-20 10:41:06,370 - INFO - Configuration variables of interest:
2024-11-20 10:41:06,370 - INFO - Configuration variables of interest:
2024-11-20 10:41:06,370 - INFO - Configuration variables of interest:
2024-11-20 10:41:06,370 - INFO - Configuration variables of interest:
2024-11-20 10:41:06,370 - INFO - Configuration variables of interest:
2024-11-20 10:41:06,370 - INFO - Configuration variables of interest:
2024-11-20 10:41:06,370 - INFO - Configuration variables of interest:
2024-11-20 10:41:06,379 - INFO - Single run: True
2024-11-20 10:41:06,379 - INFO - Single run: True
2024-11-20 10:41:06,379 - INFO - Single run: True
2024-11-20 10:41:06,379 - INFO - Single run: True
2024-11-20 10:41:06,379 - INFO - Single run: True
2024-11-20 10:41:06,379 - INFO - Single run: True
2024-11-20 10:41:06,379 - INFO - Single run: True
2024-11-20 10:41:06,

## Sensitivity analysis

### Sensitivity analysis for the PE

In [ ]:
label = 'notebook_new_test_screening_strategy'
logger, log_dir = create_folders_logger(label=label, output_dir = 'notebook/' + label, date = False, time = False)

sens_analysis_PE_method(
    label = label,
    output_dir = 'notebook/' + label,
    log_dir = log_dir,
)

2024-11-19 18:37:20,688 - INFO - Params: [1.0093341142439152, 0.8571719874246556, 0.04178968444738308]
2024-11-19 18:38:21,461 - INFO - PE_info: 3.7, PE_cost: 5, DONE!
2024-11-19 18:38:22,190 - INFO - Params: [1.0151588794002224, 0.862347117204664, 0.041721921240563384]
2024-11-19 18:39:20,468 - INFO - PE_info: 3.7, PE_cost: 10, DONE!
2024-11-19 18:39:21,123 - INFO - Params: [1.0134772916090737, 0.857054672122177, 0.04287231631147201]
2024-11-19 18:40:18,917 - INFO - PE_info: 3.7, PE_cost: 50, DONE!
2024-11-19 18:40:19,590 - INFO - Params: [1.022067459821693, 0.8807280032514646, 0.03806265341941766]
2024-11-19 18:41:19,591 - INFO - PE_info: 4.0, PE_cost: 5, DONE!
2024-11-19 18:41:20,335 - INFO - Params: [1.021187024801558, 0.8786095088223509, 0.038458151584832]
2024-11-19 18:42:19,491 - INFO - PE_info: 4.0, PE_cost: 10, DONE!
2024-11-19 18:42:20,467 - INFO - Params: [1.0190670467347074, 0.8732762847895542, 0.039483772499104994]
2024-11-19 18:43:28,058 - INFO - PE_info: 4.0, PE_cost: 50

### Sensitivity analysis for comfort parameters

In [3]:
label = 'notebook_sens_analysis_comf_param'
logger, log_dir = create_folders_logger(label = label, output_dir= 'notebook/' + label, date = False, time = False)

sens_analysis_elicitation(
    label = label,
    output_dir = 'notebook/' + label
)

2024-11-20 09:59:15,695 - INFO - Configuration variables of interest:
2024-11-20 09:59:15,695 - INFO - Configuration variables of interest:
2024-11-20 09:59:15,697 - INFO - Single run: True
2024-11-20 09:59:15,697 - INFO - Single run: True
2024-11-20 09:59:15,698 - INFO - Use all variables: True
2024-11-20 09:59:15,698 - INFO - Use all variables: True
2024-11-20 09:59:15,699 - INFO - Use case with new test: False
2024-11-20 09:59:15,699 - INFO - Use case with new test: False
2024-11-20 09:59:15,700 - INFO - PE method: {'PE_cost': 10, 'PE_info': 4, 'PE_prob': 0.7}
2024-11-20 09:59:15,700 - INFO - PE method: {'PE_cost': 10, 'PE_info': 4, 'PE_prob': 0.7}
2024-11-20 09:59:15,700 - INFO - Change lambdas? True
2024-11-20 09:59:15,700 - INFO - Change lambdas? True
2024-11-20 09:59:15,701 - INFO - Read lambda list from config? True
2024-11-20 09:59:15,701 - INFO - Read lambda list from config? True
2024-11-20 09:59:15,702 - INFO - Lambdas: [4.011942483017116, 4.168480067521723, 6.8019845179731

Counts: best_option
No_scr_no_col    288682
No_scr_col            0
gFOBT                 0
FIT                3201
Blood_based           0
Stool_DNA         47824
CTC                   0
Colon_capsule         0
Name: count, dtype: int64


In [4]:
label = 'notebook_sens_analysis_comf_param'
logger, log_dir = create_folders_logger(label = label, output_dir= 'notebook/' + label, date = False, time = False)

lambda_list = cfg["lambda_list"]
lambda_list[2] = 6.3

sens_analysis_elicitation(
    lambda_list = lambda_list,
    label = label,
    output_dir = 'notebook/' + label
)

2024-11-20 10:04:40,859 - INFO - Configuration variables of interest:
2024-11-20 10:04:40,859 - INFO - Configuration variables of interest:
2024-11-20 10:04:40,859 - INFO - Configuration variables of interest:
2024-11-20 10:04:40,859 - INFO - Configuration variables of interest:
2024-11-20 10:04:40,862 - INFO - Single run: True
2024-11-20 10:04:40,862 - INFO - Single run: True
2024-11-20 10:04:40,862 - INFO - Single run: True
2024-11-20 10:04:40,862 - INFO - Single run: True
2024-11-20 10:04:40,865 - INFO - Use all variables: True
2024-11-20 10:04:40,865 - INFO - Use all variables: True
2024-11-20 10:04:40,865 - INFO - Use all variables: True
2024-11-20 10:04:40,865 - INFO - Use all variables: True
2024-11-20 10:04:40,866 - INFO - Use case with new test: False
2024-11-20 10:04:40,866 - INFO - Use case with new test: False
2024-11-20 10:04:40,866 - INFO - Use case with new test: False
2024-11-20 10:04:40,866 - INFO - Use case with new test: False
2024-11-20 10:04:40,868 - INFO - PE meth

Counts: best_option
No_scr_no_col    313960
No_scr_col            0
gFOBT                 0
FIT                   0
Blood_based           0
Stool_DNA         25747
CTC                   0
Colon_capsule         0
Name: count, dtype: int64


In [5]:
label = 'notebook_sens_analysis_comf_param'
logger, log_dir = create_folders_logger(label = label, output_dir= 'notebook/' + label, date = False, time = False)

lambda_list = cfg["lambda_list"]
lambda_list[0] = 4.8
lambda_list[1] = 5

sens_analysis_elicitation(
    lambda_list = lambda_list,
    label = label,
    output_dir = 'notebook/' + label
)

2024-11-20 10:07:02,230 - INFO - Configuration variables of interest:
2024-11-20 10:07:02,230 - INFO - Configuration variables of interest:
2024-11-20 10:07:02,230 - INFO - Configuration variables of interest:
2024-11-20 10:07:02,230 - INFO - Configuration variables of interest:
2024-11-20 10:07:02,230 - INFO - Configuration variables of interest:
2024-11-20 10:07:02,230 - INFO - Configuration variables of interest:
2024-11-20 10:07:02,234 - INFO - Single run: True
2024-11-20 10:07:02,234 - INFO - Single run: True
2024-11-20 10:07:02,234 - INFO - Single run: True
2024-11-20 10:07:02,234 - INFO - Single run: True
2024-11-20 10:07:02,234 - INFO - Single run: True
2024-11-20 10:07:02,234 - INFO - Single run: True
2024-11-20 10:07:02,237 - INFO - Use all variables: True
2024-11-20 10:07:02,237 - INFO - Use all variables: True
2024-11-20 10:07:02,237 - INFO - Use all variables: True
2024-11-20 10:07:02,237 - INFO - Use all variables: True
2024-11-20 10:07:02,237 - INFO - Use all variables: 

Counts: best_option
No_scr_no_col    209634
No_scr_col            0
gFOBT                 0
FIT                   0
Blood_based           0
Stool_DNA        130073
CTC                   0
Colon_capsule         0
Name: count, dtype: int64
